# Bifurcaciones en 2D

**[1]** Considera el sistema

$$\dot{x} = \mu - x^2$$
$$\dot{y} = y$$

Dibuja el espacio fase para $\mu < 0$, $\mu = 0$ y $\mu > 0$.
Encuentra los puntos fijos y su estabilidad, y las variedades invariantes de los puntos fijos. ¿Qué ocurre?

In [32]:
using DifferentialEquations
using Plots
using Interact
gr()
#include("funciones_especiales.jl")

Plots.PlotlyBackend()

In [33]:
function RHS1(du::Array{Float64,1}, u::Array{Float64,1}, p::Array{Float64,1}, t::Float64)
        du[1] = p[1] - (u[1])^2
        du[2] = u[2]
end
J11(u::Array{Float64,1}, p::Array{Float64,1}) = [-2u[1] 0.; 0. 1.]

J11 (generic function with 1 method)

In [34]:
function Newton(f, J, x0, N=100)
    x = zeros(N,2) # x es un arreglo de tuplas x,y
    x[1,:] = x0 - (J(x0))^(-1)*f(x0)
    for i in 1:N-1
        if abs(det(J(x[i,:]))) > 1e-4
            x[i+1,:] = x[i,:] .- (J(x[i,:]))^(-1)*f(x[i,:])
        end
    end
    return x[end,:]
end

Newton (generic function with 2 methods)

In [35]:
function PFs_estabilidad(RHS, J, ux, uy, μ, bandera, ϵ=1e-4)
    PFs = []
    estables = []
    inestables = []
    sillas = []
    centros = []
    focos = []
    eig_estables = []
    eig_inestables = []
    eig_sillas = []
    eig_centros = []
    eig_focos = []
    
    #la funcion RHS_df convierte el sist. de ecuaciones diferenciales que regresa RHS
    # a una funcion df que regresa una tupla de vectores que usa quiver
    function RHS_df(x::Float64, y::Float64)
        du = Float64[0.,0.]
        u = Float64[x, y]
        RHS(du, u, μ, 1.)
        P2(du)
    end
    
    # df_RHS() permite usar RHS pasándole como parámetros un vector, la usa Newton()
    function df_RHS(u)
        x = u[1]
        y = u[2]
        return RHS_df(x, y)
    end
    
    for k in ux, l in uy
        x0 = [k, l]
        pf = Newton(df_RHS, x->(J(x,μ)), x0)
        if (norm(df_RHS(pf))<1e-4) & (!any([norm(x.-pf)<ϵ for x in PFs]))
            push!(PFs, pf)
        end
    end
    for i in 1:length(PFs)
        λs = eig(J(PFs[i], μ))[1]
        eigvecs = eig(J(PFs[i], μ))[2]
        reλ = real.(λs)
        Imλ = imag.(λs)
            a = all([x<0 for x in reλ])
            b = all([x>0 for x in reλ])
            c = all([x==0 for x in Imλ])
            d = all([x==0 for x in reλ])
            f = any([x>0 for x in reλ])
        
        if a & c
            push!(estables, PFs[i])
            push!(eig_estables, eigvecs, λs)
            elseif b & c
            push!(inestables, PFs[i])
            push!(eig_inestables, eigvecs, λs)
            elseif c & f
            push!(sillas, PFs[i])
            push!(eig_sillas, eigvecs, λs)
            elseif d
            push!(centros, PFs[i])
            push!(eig_centros, eigvecs, λs)
            else 
            push!(focos, PFs[i])
            push!(eig_focos, eigvecs, λs)
        end
    end
    dict = Dict(cadena => Array[] for cadena in ["estable", "inestable",
                "silla", "centro", "foco"])
    dict_eig = Dict(cadena_eig => Array[] for cadena_eig in ["estable", "inestable", "silla"])
    dict["estable"] = estables
    #dict["eig_estable"] = eig_estables
    dict["inestable"] = inestables
    #dict["eig_inestable"] = eig_inestables
    dict["silla"] = sillas
    #dict["eig_silla"] = eig_sillas
    dict["centro"] = centros
    dict["foco"] = focos
    dict_eig["estable"] = eig_estables
    dict_eig["inestable"] = eig_inestables
    dict_eig["silla"] = eig_sillas
    dict_eig["centro"] = eig_centros
    dict_eig["foco"] = eig_focos
    if bandera == "eigenvector"
    return dict_eig
        else 
        return dict
    end
end

PFs_estabilidad (generic function with 2 methods)

In [36]:
function PFs_estabilidad2(RHS, J, ux, uy, μ, bandera, ϵ=1e-4)
    PFs = []
    estables = []
    inestables = []
    sillas = []
    centros = []
    espirales_est = []
    espirales_inest = []
    eig_estables = []
    eig_inestables = []
    eig_sillas = []
    #eig_centros = []
    #eig_espirales = []
    
    #la funcion RHS_df convierte el sist. de ecuaciones diferenciales que regresa RHS
    # a una funcion df que regresa una tupla de vectores que usa quiver
    function RHS_df(x::Float64, y::Float64)
        du = Float64[0.,0.]
        u = Float64[x, y]
        RHS(du, u, μ, 1.)
        P2(du)
    end
    
    # df_RHS() permite usar RHS pasándole como parámetros un vector, la usa Newton()
    function df_RHS(u)
        x = u[1]
        y = u[2]
        return RHS_df(x, y)
    end
    
    for k in ux, l in uy
        x0 = [k, l]
        pf = Newton(df_RHS, x->(J(x,μ)), x0)
        if (norm(df_RHS(pf))<1e-4) & (!any([norm(x.-pf)<ϵ for x in PFs]))
            push!(PFs, pf)
        end
    end
    for i in 1:length(PFs)
        λs = eig(J(PFs[i], μ))[1] #eigen valores
        reλ = real.(λs) #parte real
        Imλ = imag.(λs) #parte imaginaria
        eigvecs = eig(J(PFs[i], μ))[2]
        Δ = real(λs[1] * λs[2])
        τ = real(λs[1] + λs[2])
        if Δ < 0
            push!(sillas, PFs[i])
            push!(eig_sillas, eigvecs, λs)
        elseif (Δ > 0) & (norm(Imλ) <= 1e-4)
            if τ < 0
                push!(estables, PFs[i])
                push!(eig_estables, eigvecs, λs)
            elseif τ > 0
                push!(inestables, PFs[i])
                push!(eig_inestables, eigvecs, λs)
            end
        elseif Δ > 0
            if τ < 0
                push!(espirales_est, PFs[i])
            elseif τ > 0
                push!(espirales_inest, PFs[i])
                else push!(centros, PFs[i])
            end
            else nothing
        end
    end
    dict = Dict(cadena => Array[] for cadena in ["nodo estable", "nodo inestable",
                "punto silla", "centro", "espiral estable", "espiral inestable"])
    dict_eig = Dict(cadena_eig => Array[] for cadena_eig in ["nodo estable", "nodo inestable", "punto silla"])
    dict["nodo estable"] = estables
    #dict["eig_estable"] = eig_estables
    dict["nodo inestable"] = inestables
    #dict["eig_inestable"] = eig_inestables
    dict[" punto silla"] = sillas
    #dict["eig_silla"] = eig_sillas
    dict["centro"] = centros
    dict["espiral estable"] = espirales_est
    dict["espiral inestable"] = espirales_inest
    dict_eig["nodo estable"] = eig_estables
    dict_eig["nodo inestable"] = eig_inestables
    dict_eig["punto silla"] = eig_sillas
    if bandera == "eigenvector"
    return dict_eig
        else 
        return dict
    end
end

PFs_estabilidad2 (generic function with 2 methods)

In [37]:
function campo(RHS,
        meshx=linspace(-3, 1, 6), meshy=linspace(-3, 1, 6),
        μ=1., k=10., tmax=4.0, h=0.1)

    #condiciones iniciales en un mesh
    ux = meshx
    uy = meshy
    cond_init = [[ux[i], uy[j]] for i=1:length(ux), j=1:length(uy)]
    for i in 1:length(cond_init)
        prob = ODEProblem(RHS, cond_init[i], (0, tmax), μ)
        sol = solve(prob, saveat=h, force_dtmin=true)
        a = [sol.u[i][1] for i = 1:length(sol.u)]
        sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
        solx = sols[:,1]
        soly = sols[:,2]
        plot!(solx, soly, lw=2, label="")
    end
    #current()
    
    #la funcion RHS_df convierte el sist. de ecuaciones diferenciales que regresa RHS
    # a una funcion df que regresa una tupla de vectores que usa quiver
    function RHS_df(x::Float64, y::Float64)
        du = Float64[0.,0.]
        u = Float64[x, y]
        RHS(du, u, μ, 1.)
        P2(du)/k
    end
    
    Y = meshy
    X = meshx
    pts = vec(P2[(X[i], Y[j]) for i=1:length(X), j=1:length(Y)])
    quiver!(pts, quiver=RHS_df)
end

campo (generic function with 7 methods)

In [38]:
function estabilidad_nolineal2D(RHS, J, meshx, meshy, μ, k, tmax, h)
    pts = PFs_estabilidad(RHS, J, meshx, meshy, μ, "eigenvalor")
    campo(RHS, meshx, meshy, μ, k, tmax, h)
    #grafica ptos fijos
    for key in keys(pts), j in 1:length(pts[key])
        if length(pts[key]) != 0
            scatter!([pts[key][j][1]], [pts[key][j][2]],
                label=key, ms=5)
        end
    end
    current()
end

estabilidad_nolineal2D (generic function with 1 method)

In [39]:
function variedades(RHS, J, ux, uy, p, k, tmax, h, α, δ)
    pts = PFs_estabilidad(RHS, J, ux, uy, p, "eigenvalor")
    vector = PFs_estabilidad(RHS, J, ux, uy, p, "eigenvector")
    estabilidad_nolineal2D(RHS, J, ux, uy, p, k, tmax, h)
    for key in keys(vector)
        if length(vector[key]) != 0
            pf = pts[key][1]
            eigen_vec = vector[key][1]
            eigen_val = vector[key][2]
            for i in 1:length(eigen_val)
                signo = [-δ, δ]
                if eigen_val[i] < 0 #variedades estables
                    for δ in signo
                        pert = pf + δ.*eigen_vec[:,i]
                        prob = ODEProblem(RHS, pert, (0., -α*tmax), p)
                        sol = solve(prob, Tsit5(), force_dtmin=true)
                        a = [sol.u[i][1] for i = 1:length(sol.u)]
                        sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
                        solx = sols[:,1]
                        soly = sols[:,2]
                        plot!(solx, soly, lw=2, linestyle=:dash, color=:blue, label="")
                    end
                elseif eigen_val[i] >= 0
                    for δ in signo #variedades inestables
                        pert = pf + δ.*eigen_vec[:,i]
                        prob = ODEProblem(RHS, pert, (0., α*tmax), p)
                        sol = solve(prob, Tsit5(), force_dtmin=true)
                        a = [sol.u[i][1] for i = 1:length(sol.u)]
                        sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
                        solx = sols[:,1]
                        soly = sols[:,2]
                        plot!(solx, soly, lw=2, linestyle=:dash, color=:red, label="")
                    end
                end
            end
        end
    end
    current()
end

variedades (generic function with 1 method)

In [40]:
ux=linspace(-2., 2., 20)
uy=linspace(-1., 1., 20)
k=6.
tmax=0.4
h=0.1
α = 100
δ = 1e-4
p = [-0.1]
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
plot(xlims=xlim, ylims=ylim, title="mu=-0.1")
p1 = variedades(RHS1, J11, ux, uy, p, k, tmax, h, α, δ)

p = [0.]
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
plot(xlims=xlim, ylims=ylim, title="mu=0")
p2 = variedades(RHS1, J11, ux, uy, p, k, tmax, h, α, δ)

p = [1.]
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
plot(xlims=xlim, ylims=ylim, title="mu=1")
p3 = variedades(RHS1, J11, ux, uy, p, k, tmax, h, α, δ);

In [41]:
plot(p3)

#### Para $\mu=+1$ se observa un pto. fijo inestable en $(-1,0)$ y un pto. fijo silla en $(1,0)$, las líneas punteadas representan las variedades invariantes para cada pto. fijo, azul es la variedad estable (i.e el cjto. de puntos fijos iniciales $\mathbf{x}$ que satisfacen que $\mathbf{x}(t \rightarrow \infty) \rightarrow \mathbf{x}_{fijo}$) y la línea roja es la variedad inestables (i.e $\mathbf{x}(t \rightarrow -\infty) \rightarrow \mathbf{x}_{fijo}$)

#### Notar que entre los puntos fijos, lo que para el pto silla es una variedad estable, para el pto inestable es una variedad inestable. Por eso vemos ese empalme de líneas rojas con azules.

In [42]:
plot(p2)

#### Para $\mu = 0$ los dos ptos. fijos anteriores colisionan en un punto fijo de tipo silla en $(0,0)$ Ahora sólo existe una variedad inestable, ya que los puntos $(x, y=0)$ ya no satisfacen ser una variedad estable o inestable. Notemos para $(x<0, 0)$ los puntos iniciales ahí tenderan a alejarse del pto fijo cuando $t \rightarrow \infty$, mientras que $(x>0, 0)$ tienden hacia el pto fijo cuando $t \rightarrow \infty$. Por eso la línea $(x, 0)$ ya no es una variedad.

In [12]:
plot(p1)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -2 
 
 
 -1 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 mu=-0.1 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<polyline clip-path="url(#clip8202)" style="stroke:#00a8cb; stroke-width:1; stroke-opacity:1; fill:none" points="
 402.291,178.94

#### en $\mu=-0.1$ los puntos fijos que habían colisionado, se aniquilaron y ahora ya no hay puntos fijos, aunque sigue habiendo una especie de memoria en el comportamiento del campo.

## **[2]** Considera el sistema

$$\dot{x} = \mu x + y + \sin x$$
$$\dot{y} = x - y$$

Encuentra numéricamente una $\mu_c$ para la cual hay una bifurcación. ¿Qué ocurre?

In [13]:
function RHS2(du::Array{Float64,1}, u::Array{Float64,1}, p::Array{Float64,1}, t::Float64)
        du[1] = p[1]*u[1] + u[2] + sin(u[1])
        du[2] = u[1] - u[2]
end
J2(u::Array{Float64,1}, p::Array{Float64,1}) = [p[1]+cos(u[1]) 1.; 1. -1.]

J2 (generic function with 1 method)

In [28]:
ux=linspace(-10., 10., 15)
uy=linspace(-10., 10., 15)
k=1e3
tmax=4.
h=0.1
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
@manipulate for μ in -3.:0.1:1.
    p = [μ]
    plot(xlims=xlim, ylims=ylim, xlabel="x", ylabel="y")
    #α = 30
    #δ = 1e-4
    #variedades(RHS2, J2, ux, uy, p, k, tmax, h, α, δ)
    estabilidad_nolineal2D(RHS2, J2, ux, uy, p, k, tmax, h)
end

Interact.Options{:SelectionSlider,Float64}(17: "input-5" = -1.0 Float64 , "μ", -1.0, "-1.0", 21, Interact.OptionDict(DataStructures.OrderedDict("-3.0"=>-3.0,"-2.9"=>-2.9,"-2.8"=>-2.8,"-2.7"=>-2.7,"-2.6"=>-2.6,"-2.5"=>-2.5,"-2.4"=>-2.4,"-2.3"=>-2.3,"-2.2"=>-2.2,"-2.1"=>-2.1…), Dict(1.0=>"1.0",0.3=>"0.3",-2.3=>"-2.3",-2.1=>"-2.1",-1.0=>"-1.0",-0.2=>"-0.2",-1.3=>"-1.3",-0.3=>"-0.3",-0.6=>"-0.6",-1.6=>"-1.6"…)), Any[], Any[], true, "horizontal", true)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 -10 
 
 
 -5 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 x 
 
 
 y 
 
<polyline clip-path="url(#clip2002)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 51.9048,360.121 53.2192,360.078 54.3215,359.963 55.2542,359.796 56.0512,359.591 56.74,359.359 57.3417,359.108 57.8728,358.846 58.3471,358.578 58.7752,358.307 
 59.1644,358.036 59.5212,357.767 59.8515,357.503 60.1596,357.244 60.448,356.99 60.7188,356.744 60.9743,356.504 61.2166,356.271 61.4476,356.046 61.6679,355.828 
 61.8779,355.618 62.0783,355.414 62.2698,355.218 62.4532,355.028 62.6296,354.845 62.7993,354.669 62.9624,354.499 63.119,354.336 63.2692,354.178 63.4134,354.026 
 63.5518,353.88 63.6849,353.738 63.813,353.603 63.9366,353.472 64.0556,353.346 64.1701,353.225 64.2802,353.108 64.3861,352.996 64.488,352.888 64.5861,352.783 
 64.6804,352.683 
 "/>
<polyline clip-path="url(#clip2002)" style="stroke:#e26f46; stroke-width:2; stroke-opacity:1; fill:none" points="
 89.6483,360.121 84.5122,357.923 80.4835,356.221 77.3492,354.903 74.9226,353.884 73.0505,353.096 71.6085,352.486 70.5002,352.013 69.6498,351.647 68.9964,351.362 
 68.4962,351.14 68.1145,350.966 67.8224,350.831 67.5988,350.723 67.4295,350.639 67.3023,350.572 67.2061,350.518 67.1327,350.474 67.078,350.438 67.0385,350.409 
 67.0105,350.385 66.9905,350.365 66.9756,350.348 66.9653,350.332 66.959,350.319 66.9561,350.308 66.9558,350.298 66.957,350.289 66.9587,350.28 66.9606,350.272 
 66.9631,350.265 66.9661,350.258 66.9698,350.251 66.974,350.245 66.9786,350.24 66.9831,350.235 66.9874,350.23 66.9911,350.225 66.9949,350.22 66.9986,350.215 
 67.0023,350.211 
 "/>
<polyline clip-path="url(#clip2002)" style="stroke:#3da44d; stroke-width:2; stroke-opacity:1; fill:none" points="
 127.392,360.121 118.394,355.678 110.527,352.187 103.798,349.485 98.151,347.428 93.4835,345.888 89.666,344.76 86.5629,343.955 84.0493,343.403 82.0106,343.044 
 80.3533,342.835 79.0016,342.741 77.8897,342.731 76.9666,342.786 76.1958,342.889 75.5457,343.027 74.9888,343.189 74.5056,343.367 74.0836,343.557 73.7118,343.755 
 73.3795,343.956 73.0773,344.156 72.8007,344.356 72.5468,344.553 72.3127,344.748 72.0951,344.938 71.8905,345.123 71.6963,345.303 71.5122,345.477 71.3378,345.646 
 71.1726,345.81 71.0156,345.968 70.866,346.121 70.7226,346.269 70.5843,346.411 70.4517,346.548 70.3245,346.681 70.2026,346.808 70.0856,346.931 69.9732,347.049 
 69.8651,347.163 
 "/>
<polyline clip-path="url(#clip2002)" style="stroke:#c271d2; stroke-width:2; stroke-opacity:1; fill:none" points="
 165.136,360.121 155.817,353.321 147.466,347.72 139.895,343.151 133.003,339.47 126.744,336.551 121.094,334.282 116.034,332.565 111.543,331.311 107.584,330.441 
 104.115,329.885 101.089,329.586 98.4549,329.493 96.1569,329.562 94.1496,329.759 92.3922,330.056 90.8447,330.428 89.4696,330.856 88.2413,331.323 87.1391,331.82 
 86.143,332.336 85.2334,332.862 84.3953,333.392 83.6211,333.922 82.9034,334.449 82.2347,334.969 81.6071,335.481 81.0132,335.982 80.4507,336.47 79.918,336.947 
 79.4129,337.411 78.9331,337.863 78.4754,338.301 78.0367,338.725 77.6156,339.135 77.2123,339.532 76.8261,339.916 76.4563,340.287 76.1019,340.646 75.7618,340.993 
 75.4345,341.327 
 "/>
<polyline clip-path="url(#clip2002)" style="stroke:#ac8d18; stroke-width:2; stroke-opacity:1; fill:none" points="
 202.879,360.121 191.644,351.023 182.697,343.418 175.363,337.044 169.209,331.698 163.944,327.216 159.372,323.468 155.347,320.346 151.762,317.759 148.535,315.631 
 145.602,313.898 142.908,312.506 140.413,311.409 138.08,310.568 135.882,309.949 133.791,309.523 131.79,309.265 129.862,309.155 127.995,309.175 126.176,309.309 
 124.397,309.542 122.652,309.863 120.939,310.262 119.255,310.731 117.596,311.26 115.961,311.841 114.351,312.468 112.768,313.135 111.215,313.838 109.693,314.572 
 108.202,315.33 106.743,316.108 105.316,316.901 103.926,317.707 102.

#### Nos fijaremos en el punto fijo que se encuentra en (0,0)

#### Con @manipulate se observa que el punto fijo que se encuentra en $(0,0)$ cambia de estabilidad en $\mu_c = -2.0$.

#### Es decir, empezando con $\mu > -2$ conforme $\mu \rightarrow -2$ los puntos fijos estables se empiezan a aproximar al punto silla que está en el origen y en $\mu = -2.0$  éstos coaslecen en un sólo punto fijo estable en $(0,0)$

#### Esto se conoce como "bifurcación de tenedor supercrítica", es decir, para $\mu< \mu_c$ existe un punto fijo de tipo estable, luego, para $\mu > \mu_c$ éste se "trifurca" en un punto silla y dos estables

**[3]** Considera el sistema escrito en *coordenadas polares*:

$$\dot{r} = \mu r - r^3$$
$$\dot{\theta} = \omega + r^2$$

(i) Dibuja el espacio fase para distintos valores de $\mu$ cercanos a $0$. ¿Qué comportamiento observas?

(ii) Haz un cambio de coordenadas a coordenadas Cartesianas.

(iii) Así, haz un análisis de estabilidad lineal del punto fijo en el origin.

(iv) Dibuja los eigenvalores de este punto fijo en función de $\mu$. ¿Qué ocurre? 

Esto se llama una **bifurcación de Hopf**: nace un **ciclo límite**.

In [15]:
function RHS3(du::Array{Float64,1}, u::Array{Float64,1}, p::Array{Float64,1}, t::Float64)
        du[1] = p[1]*u[1] - (u[1])^3
        du[2] = p[2] + (u[1])^2
end
J3(u::Array{Float64,1}, p::Array{Float64,1}) = [p[1]+cos(u[1]) 1.; 1. -1.]

J3 (generic function with 1 method)

In [29]:
ux=linspace(0., 3., 15)
uy=linspace(-π, π, 15)
k=1e2
tmax=3.
h=0.01
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
ω = 1
@manipulate for μ in -1.:0.1:1.
    p = [μ, ω]
    plot(xlims=xlim, ylims=ylim, xlabel="r", ylabel="theta")
    #α = 30
    #δ = 1e-4
    #variedades(RHS2, J2, ux, uy, p, k, tmax, h, α, δ)
    campo(RHS3, ux, uy, p, k, tmax, h)
end

Interact.Options{:SelectionSlider,Float64}(21: "input-6" = 0.0 Float64 , "μ", 0.0, "0.0", 11, Interact.OptionDict(DataStructures.OrderedDict("-1.0"=>-1.0,"-0.9"=>-0.9,"-0.8"=>-0.8,"-0.7"=>-0.7,"-0.6"=>-0.6,"-0.5"=>-0.5,"-0.4"=>-0.4,"-0.3"=>-0.3,"-0.2"=>-0.2,"-0.1"=>-0.1…), Dict(1.0=>"1.0",0.3=>"0.3",-0.2=>"-0.2",-1.0=>"-1.0",-0.3=>"-0.3",-0.6=>"-0.6",0.7=>"0.7",0.0=>"0.0",0.2=>"0.2",-0.1=>"-0.1"…)), Any[], Any[], true, "horizontal", true)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 -3 
 
 
 -2 
 
 
 -1 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 r 
 
 
 theta 
 
<polyline clip-path="url(#clip3802)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 45.2142,360.121 45.2142,359.566 45.2142,359.012 45.2142,358.458 45.2142,357.903 45.2142,357.349 45.2142,356.795 45.2142,356.24 45.2142,355.686 45.2142,355.131 
 45.2142,354.577 45.2142,354.023 45.2142,353.468 45.2142,352.914 45.2142,352.36 45.2142,351.805 45.2142,351.251 45.2142,350.697 45.2142,350.142 45.2142,349.588 
 45.2142,349.034 45.2142,348.479 45.2142,347.925 45.2142,347.371 45.2142,346.816 45.2142,346.262 45.2142,345.707 45.2142,345.153 45.2142,344.599 45.2142,344.044 
 45.2142,343.49 45.2142,342.936 45.2142,342.381 45.2142,341.827 45.2142,341.273 45.2142,340.718 45.2142,340.164 45.2142,339.61 45.2142,339.055 45.2142,338.501 
 45.2142,337.947 45.2142,337.392 45.2142,336.838 45.2142,336.284 45.2142,335.729 45.2142,335.175 45.2142,334.62 45.2142,334.066 45.2142,333.512 45.2142,332.957 
 45.2142,332.403 45.2142,331.849 45.2142,331.294 45.2142,330.74 45.2142,330.186 45.2142,329.631 45.2142,329.077 45.2142,328.523 45.2142,327.968 45.2142,327.414 
 45.2142,326.86 45.2142,326.305 45.2142,325.751 45.2142,325.196 45.2142,324.642 45.2142,324.088 45.2142,323.533 45.2142,322.979 45.2142,322.425 45.2142,321.87 
 45.2142,321.316 45.2142,320.762 45.2142,320.207 45.2142,319.653 45.2142,319.099 45.2142,318.544 45.2142,317.99 45.2142,317.436 45.2142,316.881 45.2142,316.327 
 45.2142,315.772 45.2142,315.218 45.2142,314.664 45.2142,314.109 45.2142,313.555 45.2142,313.001 45.2142,312.446 45.2142,311.892 45.2142,311.338 45.2142,310.783 
 45.2142,310.229 45.2142,309.675 45.2142,309.12 45.2142,308.566 45.2142,308.012 45.2142,307.457 45.2142,306.903 45.2142,306.349 45.2142,305.794 45.2142,305.24 
 45.2142,304.685 45.2142,304.131 45.2142,303.577 45.2142,303.022 45.2142,302.468 45.2142,301.914 45.2142,301.359 45.2142,300.805 45.2142,300.251 45.2142,299.696 
 45.2142,299.142 45.2142,298.588 45.2142,298.033 45.2142,297.479 45.2142,296.925 45.2142,296.37 45.2142,295.816 45.2142,295.261 45.2142,294.707 45.2142,294.153 
 45.2142,293.598 45.2142,293.044 45.2142,292.49 45.2142,291.935 45.2142,291.381 45.2142,290.827 45.2142,290.272 45.2142,289.718 45.2142,289.164 45.2142,288.609 
 45.2142,288.055 45.2142,287.501 45.2142,286.946 45.2142,286.392 45.2142,285.837 45.2142,285.283 45.2142,284.729 45.2142,284.174 45.2142,283.62 45.2142,283.066 
 45.2142,282.511 45.2142,281.957 45.2142,281.403 45.2142,280.848 45.2142,280.294 45.2142,279.74 45.2142,279.185 45.2142,278.631 45.2142,278.077 45.2142,277.522 
 45.2142,276.968 45.2142,276.413 45.2142,275.859 45.2142,275.305 45.2142,274.75 45.2142,274.196 45.2142,273.642 45.2142,273.087 45.2142,272.533 45.2142,271.979 
 45.2142,271.424 45.2142,270.87 45.2142,270.316 45.2142,269.761 45.2142,269.207 45.2142,268.653 45.2142,268.098 45.2142,267.544 45.2142,266.99 45.2142,266.435 
 45.2142,265.881 45.2142,265.326 45.2142,264.772 45.2142,264.218 45.2142,263.663 45.2142,263.109 45.2142,262.555 45.2142,262 45.2142,261.446 45.2142,260.892 
 45.2142,260.337 45.2142,259.783 45.2142,259.229 45.2142,258.674 45.2142,258.12 45.2142,257.566 45.2142,257.011 45.2142,256.457 45.2142,255.902 45.2142,255.348 
 45.2142,254.794 45.2142,254.239 45.2142,253.685 45.2142,253.131 45.2142,252.576 45.2142,252.022 45.2142,251.468 45.2142,250.913 45.2142,250.359 45.2142,249.805 
 45.2142,249.25 45.2142,248.696 45.2142,248.142 45.2142,247.587 45.2142,247.033 45.2142,246.478 45.2142,245.924 45.2142,245.37 45.2142,244.815 45.2142,244.261 
 45.2142,243.707 45.2142,243.152 45.2142,242.598 45.2142,242.044 45.2142,241.489 45.2142,240.935 45.2142,240.381 45.2142,239.826 45.2142,239.272 45.2142,238.718 
 45.2142,238.163 45.2142,237.609 45.2142,237.055 45.2142,236.5 45.2142,235.946 45.2142,235.391 45.2142,234.837 45

#### Para valores $\mu < 0$ se observa que todas las trayectorias tienden asintóticamente a la recta $r=0$, mientras que para valores $\mu>0$ se observa que la recta a la que tienden las trayectorias se desplaza hacia valores de $r$ positivos. En particular, para $\mu=1$ la recta a la que tienden todas las trayectorias está en $r=1$ Y esto sucede tanto para trayectorias que empiezan en $r<1$ y $r>1$, es decir, pareciera haber un ciclo límite al cual se acercan todas la trayectorias

Al pasar a cartesianas, el sistema se ve como sigue:
\begin{eqnarray}
\dot{x} = \left[ \mu - (x^2 + y^2) \right]x - \left[ \omega + (x^2 + y^2) \right]y\\
\dot{y} = \left[ \mu - (x^2 + y^2) \right]y + \left[ \omega + (x^2 + y^2) \right]x
\end{eqnarray}

In [17]:
function RHS4(du::Array{Float64,1}, u::Array{Float64,1}, p::Array{Float64,1}, t::Float64)
        du[1] = (p[1] - (u[1]^2 + u[2]^2))*u[1] - (p[2] + (u[1]^2 + u[2]^2))*u[2]
        du[2] = (p[1] - (u[1]^2 + u[2]^2))*u[2] + (p[2] + (u[1]^2 + u[2]^2))*u[1]
end

RHS4 (generic function with 1 method)

In [18]:
J4(u::Array{Float64,1}, p::Array{Float64,1}) = [(p[1] -(3u[1]^2 - u[2]^2 - 2u[1]*u[2])) (-p[2] -(3u[2]^2 + u[1]^2 + 2u[1]*u[2]));
   (p[2] + 3u[1]^2 + u[2]^2 - 2u[1]*u[2]) (p[1] - 3u[2]^2 - u[2]^2 + 2u[1]*u[2])]

J4 (generic function with 1 method)

In [30]:
ux=linspace(-3., 3., 15)
uy=linspace(-3., 3., 15)
k=1e3
tmax=3.
h=0.01
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
ω = 1.
@manipulate for μ in -1.:0.1:1.
    p = [μ, ω]
    plot(xlims=xlim, ylims=ylim, xlabel="r", ylabel="theta", title="espacio fase en omega=1")
    estabilidad_nolineal2D(RHS4, J4, ux, uy, p, k, tmax, h)
    #campo(RHS4, ux, uy, p, k, tmax, h)
end

Interact.Options{:SelectionSlider,Float64}(25: "input-7" = 0.0 Float64 , "μ", 0.0, "0.0", 11, Interact.OptionDict(DataStructures.OrderedDict("-1.0"=>-1.0,"-0.9"=>-0.9,"-0.8"=>-0.8,"-0.7"=>-0.7,"-0.6"=>-0.6,"-0.5"=>-0.5,"-0.4"=>-0.4,"-0.3"=>-0.3,"-0.2"=>-0.2,"-0.1"=>-0.1…), Dict(1.0=>"1.0",0.3=>"0.3",-0.2=>"-0.2",-1.0=>"-1.0",-0.3=>"-0.3",-0.6=>"-0.6",0.7=>"0.7",0.0=>"0.0",0.2=>"0.2",-0.1=>"-0.1"…)), Any[], Any[], true, "horizontal", true)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -3 
 
 
 -2 
 
 
 -1 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 -3 
 
 
 -2 
 
 
 -1 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 espacio fase en omega=1 
 
 
 r 
 
 
 theta 
 
<polyline clip-path="url(#clip5202)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 45.2142,360.121 123.719,358.101 175.68,351.807 213.036,344.847 241.162,337.932 263.134,331.299 280.789,325.052 295.273,319.203 307.359,313.736 317.583,308.624 
 326.33,303.836 333.888,299.341 340.468,295.111 346.237,291.121 351.326,287.348 355.836,283.773 359.85,280.378 363.436,277.146 366.65,274.065 369.538,271.121 
 372.139,268.304 374.485,265.605 376.604,263.014 378.521,260.524 380.255,258.127 381.825,255.817 383.246,253.589 384.532,251.438 385.693,249.358 386.742,247.346 
 387.687,245.397 388.537,243.508 389.299,241.675 389.98,239.896 390.585,238.168 391.121,236.488 391.591,234.854 392,233.264 392.353,231.715 392.653,230.207 
 392.903,228.736 393.106,227.301 393.266,225.902 393.384,224.536 393.463,223.202 393.505,221.899 393.512,220.626 393.487,219.382 393.43,218.165 393.343,216.975 
 393.229,215.81 393.088,214.671 392.921,213.555 392.73,212.463 392.517,211.394 392.281,210.346 392.024,209.32 391.747,208.314 391.451,207.329 391.136,206.363 
 390.804,205.416 390.455,204.488 390.09,203.578 389.71,202.685 389.315,201.81 388.906,200.951 388.483,200.109 388.047,199.282 387.599,198.471 387.138,197.676 
 386.666,196.895 386.182,196.129 385.688,195.378 385.184,194.64 384.67,193.917 384.146,193.206 383.613,192.51 383.071,191.826 382.52,191.155 381.962,190.496 
 381.395,189.85 380.821,189.216 380.24,188.594 379.652,187.984 379.057,187.385 378.456,186.797 377.849,186.221 377.235,185.656 376.616,185.101 375.992,184.557 
 375.362,184.024 374.726,183.501 374.086,182.988 373.442,182.486 372.793,181.993 372.139,181.51 371.481,181.037 370.82,180.573 370.155,180.119 369.486,179.674 
 368.814,179.239 368.139,178.812 367.46,178.395 366.779,177.986 366.095,177.586 365.408,177.195 364.719,176.812 364.028,176.438 363.334,176.072 362.639,175.715 
 361.941,175.366 361.242,175.024 360.541,174.691 359.839,174.366 359.135,174.048 358.43,173.739 357.723,173.437 357.016,173.142 356.307,172.855 355.598,172.576 
 354.888,172.304 354.178,172.039 353.467,171.782 352.756,171.532 352.044,171.289 351.332,171.052 350.621,170.823 349.909,170.601 349.197,170.385 348.486,170.177 
 347.775,169.975 347.064,169.779 346.354,169.591 345.644,169.408 344.936,169.232 344.228,169.063 343.52,168.9 342.814,168.743 342.109,168.592 341.405,168.448 
 340.702,168.309 340,168.177 339.3,168.051 338.601,167.93 337.903,167.816 337.208,167.707 336.513,167.604 335.821,167.507 335.13,167.415 334.441,167.329 
 333.754,167.249 333.069,167.174 332.386,167.105 331.706,167.041 331.027,166.982 330.351,166.929 329.677,166.881 329.006,166.838 328.337,166.8 327.67,166.767 
 327.007,166.74 326.345,166.717 325.687,166.7 325.032,166.687 324.379,166.679 323.729,166.676 323.082,166.678 322.438,166.685 321.798,166.696 321.16,166.712 
 320.525,166.732 319.894,166.757 319.266,166.786 318.642,166.82 318.02,166.859 317.402,166.901 316.788,166.948 316.177,166.999 315.57,167.055 314.966,167.114 
 314.366,167.178 313.77,167.246 313.178,167.318 312.589,167.394 312.004,167.474 311.423,167.557 310.846,167.645 310.273,167.736 309.704,167.832 309.139,167.93 
 308.579,168.033 308.022,168.139 307.47,168.249 306.921,168.363 306.377,168.479 305.838,168.6 305.302,168.724 304.771,168.851 304.245,168.981 303.723,169.115 
 303.205,169.252 302.692,169.392 302.183,169.536 301.679,169.682 301.18,169.832 300.685,169.984 300.194,170.14 299.709,170.299 299.228,170.46 298.752,170.625 
 298.28,170.792 297.814,170.962 297.352,171.135 296.895,171.31 296.443,171.488 295.996,171.669 295.553,171.853 295.116,172.038 294.683,172.227 294.256,172.418 
 293.833,172.611 293.416,172.806 293.003,173.004 292.596,173.205 292.193,173

In [20]:
ux=linspace(-3., 3., 15)
uy=linspace(-3., 3., 15)
ω = 1.
λs1 = []
λs2 = []
rango_μ = -1.0:0.1:1.0
for μ in rango_μ
    if μ == 0
        nothing
    else
        p = [μ, ω]
        λ1 = PFs_estabilidad(RHS4, J4, ux, uy, p, "eigenvector")["foco"][2][1]
        λ2 = PFs_estabilidad(RHS4, J4, ux, uy, p, "eigenvector")["foco"][2][2]
        push!(λs1, λ1)
        push!(λs2, λ2)
    end
end

In [21]:
plot(ylims=(-2,2), xlabel="Re(lambda)", ylabel="Im(lambda)")
plot!(real.(λs1), imag.(λs1), label="lambda_1(mu)", lw=3)
plot!(real.(λs2), imag.(λs2), label="lambda_2(mu)", lw=3)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 -2 
 
 
 -1 
 
 
 0 
 
 
 1 
 
 
 2 
 
 
 Re(lambda) 
 
 
 Im(lambda) 
 
 
 
 
 
 
 
 lambda_1(mu) 
 
 
 
 lambda_2(mu)

#### Lo de arriba son los eigenvalores $\lambda_{1,2}$ en función del parámetro $\mu$ (es decir es una parametrización), el punto medio corresponde de las dos líneas corresponde a $\mu = 0$, es decir, el parámetro $\mu_c = 0$ corresponde a un cambio de signo en la parte real de los eigen valores. Para dejar esto más claro, grafiquemos $Re(\lambda_{1,2}(\mu))$

In [22]:
ux=linspace(-3., 3., 15)
uy=linspace(-3., 3., 15)
ω = 1.
real_λ1 = []
real_λ2 = []
rango_μ = -1.0:0.1:1.0
for μ in rango_μ
    if μ == 0
        push!(real_λ1, 0.)
        push!(real_λ2, 0.)
    else
        p = [μ, ω]
        λ1 = PFs_estabilidad(RHS4, J4, ux, uy, p, "eigenvector")["foco"][2][1]
        λ2 = PFs_estabilidad(RHS4, J4, ux, uy, p, "eigenvector")["foco"][2][2]
        push!(real_λ1, real(λ1))
        push!(real_λ2, real(λ2))
    end
end
plot(xlabel="mu", ylabel="Re(lambda)")
scatter!(rango_μ, real_λ1, ms=6)
scatter!(rango_μ, real_λ2)
hline!([0.], lw=3, linestyle=:dash, label="Re(lambda)=0")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 mu 
 
 
 Re(lambda) 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 y1 
 
 
 
 
 y2 
 
 
 
 Re(lambda)=0

#### Ahora sí es claro que la parte real de los eigenvalores del sistema linealizado cambian de signo cuando $\mu_c = 0$, esto se conoce como una bifurcación de Hopf

**[4]** Un modelo de una reacción química oscilante es

$$ f_1(x,y) = \dot{x} = a - x - \frac{4 x y}{1 + x^2}$$

$$f_2(x,y) = \dot{y} = b x \left( 1 - \frac{y}{1+x^2} \right)$$

Fija $a = 10$ y encuentra un valor de $b$ para la cual hay una bifurcación de Hopf.

In [23]:
function RHS5(du::Array{Float64,1}, u::Array{Float64,1}, p::Array{Float64,1}, t::Float64)
        du[1] = p[1] - u[1] - (4*u[1]*u[2]/(1 + u[1]^2))
        du[2] = p[2]*u[1]*(1 - (u[2]/(1 + u[1]^2)))
end

RHS5 (generic function with 1 method)

In [24]:
partialx_f1(u,p) = -1-(4u[2]/(1+u[1]^2))*(2u[1]/((1+u[1]^2)) - 1)
partialy_f1(u,p) = -4u[1]/(1+u[1]^2)
partialx_f2(u,p) = p[2]*(1 - (u[2]/(1+u[1]^2)) + 2*(u[1]^2)*u[2]/((1+u[1]^2)^2)) 
partialy_f2(u,p) = - p[2]*u[1]/(1+u[1]^2)
#J5(u, p) = [(p[1]-u[1]-(4u[1]*u[2])/(1+u[1]^2)) -(1+(4u[2]/(1+u[1]^2))-(8u[2]*u[1]^2)/(1+u[1]^2)^2);
#(p[2]*(1-(u[2]/(1+u[1]^2))+u[1]*(2u[1]*u[2]/(1+u[1]^2)^2))) (-p[2]*u[1]/(1+u[1]^2))]
J5(u, p) = [partialx_f1(u,p) partialy_f1(u,p);partialx_f2(u,p) partialy_f2(u,p)]

J5 (generic function with 1 method)

In [25]:
ux=linspace(0.1, 5., 10)
uy=linspace(0.1, 10., 10)
a = 15.
λs1 = []
λs2 = []
rango_b = 1.5:0.1:2.5
for b in rango_b
    p = [a, b]
    λ1 = PFs_estabilidad(RHS5, J5, ux, uy, p, "eigenvector")["foco"][2][1]
    λ2 = PFs_estabilidad(RHS5, J5, ux, uy, p, "eigenvector")["foco"][2][2]
    push!(λs1, λ1)
    push!(λs2, λ2)
end
plot(ylims=(-4,4), xlabel="Re(lambda)", ylabel="Im(lambda)")
plot!(real.(λs1), imag.(λs1), label="lambda_1(mu)", lw=3)
plot!(real.(λs2), imag.(λs2), label="lambda_2(mu)", lw=3)
vline!([0.], linestyle=:dash, lw=3, label="Re(lambda)=0")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -0.06 
 
 
 -0.04 
 
 
 -0.02 
 
 
 0.00 
 
 
 0.02 
 
 
 0.04 
 
 
 0.06 
 
 
 -4 
 
 
 -2 
 
 
 0 
 
 
 2 
 
 
 4 
 
 
 Re(lambda) 
 
 
 Im(lambda) 
 
 
 
 
 
 
 
 
 lambda_1(mu) 
 
 
 
 lambda_2(mu) 
 
 
 
 Re(lambda)=0

In [26]:
ux=linspace(0.1, 5., 10)
uy=linspace(0.1, 10., 10)
a = 15.
real_λ1 = []
real_λ2 = []
rango_b = 1.:0.1:3.0
for b in rango_b
    p = [a, b]
    λ1 = PFs_estabilidad(RHS5, J5, ux, uy, p, "eigenvector")["foco"][2][1]
    λ2 = PFs_estabilidad(RHS5, J5, ux, uy, p, "eigenvector")["foco"][2][2]
    push!(real_λ1, real(λ1))
    push!(real_λ2, real(λ2))
end
plot(xlabel="b", ylabel="Re(lambda)", title="b_critico en a=15")
scatter!(rango_b, real_λ1, ms=6)
scatter!(rango_b, real_λ2)
hline!([0.], lw=3, linestyle=:dash, label="Re(lambda) = 0")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1.0 
 
 
 1.5 
 
 
 2.0 
 
 
 2.5 
 
 
 3.0 
 
 
 -0.15 
 
 
 -0.10 
 
 
 -0.05 
 
 
 0.00 
 
 
 0.05 
 
 
 0.10 
 
 
 0.15 
 
 
 b_critico en a=15 
 
 
 b 
 
 
 Re(lambda) 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 y1 
 
 
 
 
 y2 
 
 
 
 Re(lambda) = 0

#### Se observa del análisis de arriba que el valor $b_c$ para el cual $Re(\lambda_{1,2})$ cambia de signo es justamente $b_c = 2$ siempre que $a=15$, es decir una bifurcación de Hopf se da en $(a_c,b_c) = (15, 2)$ A continuación se grafica el campo alrededor de de $b_c$.

In [31]:
ux=linspace(0.1, 7., 10)
uy=linspace(0., 24., 10)
k=1e3
tmax=5.
h=0.01
xlim = (ux[1], ux[end])
ylim = (uy[1], uy[end])
a = 15.
@manipulate for b in 1.1:0.05:3.1
    p = [a, b]
    plot(xlims=xlim, ylims=ylim, xlabel="x", ylabel="y", title="espacio fase en a=15")
    #α = 30
    #δ = 1e-4
    estabilidad_nolineal2D(RHS5, J5, ux, uy, p, k, tmax, h)
    #campo(RHS5, ux, uy, p, k, tmax, h)
end

Interact.Options{:SelectionSlider,Float64}(29: "input-8" = 2.1 Float64 , "b", 2.1, "2.1", 21, Interact.OptionDict(DataStructures.OrderedDict("1.1"=>1.1,"1.15"=>1.15,"1.2"=>1.2,"1.25"=>1.25,"1.3"=>1.3,"1.35"=>1.35,"1.4"=>1.4,"1.45"=>1.45,"1.5"=>1.5,"1.55"=>1.55…), Dict(1.2=>"1.2",1.55=>"1.55",2.0=>"2.0",2.55=>"2.55",2.8=>"2.8",1.5=>"1.5",1.45=>"1.45",2.95=>"2.95",2.2=>"2.2",2.1=>"2.1"…)), Any[], Any[], true, "horizontal", true)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 1 
 
 
 2 
 
 
 3 
 
 
 4 
 
 
 5 
 
 
 6 
 
 
 7 
 
 
 0 
 
 
 5 
 
 
 10 
 
 
 15 
 
 
 20 
 
 
 espacio fase en a=15 
 
 
 x 
 
 
 y 
 
<polyline clip-path="url(#clip6002)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 44.8772,360.121 56.381,360.071 67.765,359.979 79.0241,359.846 90.1531,359.673 101.148,359.462 112.005,359.213 122.724,358.926 133.303,358.603 143.744,358.245 
 154.046,357.851 164.212,357.422 174.241,356.96 184.135,356.463 193.896,355.934 203.525,355.371 213.024,354.777 222.393,354.151 231.634,353.493 240.749,352.805 
 249.738,352.087 258.603,351.338 267.346,350.56 275.967,349.754 284.468,348.918 292.85,348.055 301.114,347.164 309.261,346.246 317.292,345.301 325.209,344.33 
 333.013,343.333 340.704,342.31 348.284,341.262 355.754,340.19 363.114,339.094 370.366,337.973 377.511,336.829 384.55,335.663 391.484,334.473 398.313,333.262 
 405.039,332.028 411.663,330.773 418.186,329.497 424.607,328.201 430.929,326.884 437.153,325.547 443.279,324.191 449.307,322.815 455.24,321.421 461.077,320.008 
 466.82,318.578 472.469,317.129 478.026,315.663 483.491,314.18 488.864,312.681 494.147,311.165 499.341,309.633 504.445,308.086 509.462,306.523 514.391,304.946 
 519.234,303.353 523.991,301.747 528.663,300.126 533.251,298.492 537.755,296.845 542.176,295.184 546.514,293.511 550.772,291.826 554.948,290.128 559.044,288.419 
 563.061,286.698 566.999,284.967 570.858,283.224 574.64,281.471 578.345,279.708 581.974,277.935 585.527,276.152 589.005,274.36 592.408,272.558 595.738,270.748 
 598.994,268.93 602.177,267.104 605.288,265.269 608.328,263.427 611.296,261.578 614.195,259.721 617.023,257.858 619.781,255.988 622.471,254.112 625.093,252.23 
 627.647,250.343 630.133,248.449 632.553,246.551 634.906,244.648 637.194,242.74 639.416,240.828 641.573,238.911 643.666,236.991 645.696,235.067 647.661,233.14 
 649.564,231.21 651.404,229.277 653.182,227.341 654.899,225.403 656.554,223.462 658.149,221.52 659.683,219.576 661.156,217.631 662.571,215.684 663.926,213.737 
 665.222,211.789 666.46,209.84 667.64,207.891 668.762,205.942 669.827,203.994 670.835,202.046 671.786,200.098 672.681,198.152 673.52,196.206 674.304,194.262 
 675.033,192.32 675.706,190.38 676.325,188.441 676.89,186.505 677.401,184.571 677.858,182.64 678.262,180.713 678.613,178.788 678.911,176.866 679.156,174.949 
 679.349,173.035 679.49,171.125 679.58,169.219 679.618,167.318 679.604,165.422 679.54,163.53 679.425,161.644 679.259,159.763 679.043,157.887 678.777,156.018 
 678.461,154.154 678.095,152.297 677.679,150.445 677.214,148.601 676.7,146.763 676.136,144.933 675.524,143.109 674.863,141.293 674.153,139.485 673.394,137.685 
 672.587,135.892 671.731,134.108 670.828,132.333 669.876,130.566 668.876,128.809 667.829,127.06 666.734,125.321 665.592,123.591 664.401,121.871 663.164,120.161 
 661.879,118.462 660.547,116.773 659.167,115.094 657.74,113.426 656.266,111.77 654.744,110.124 653.175,108.491 651.559,106.869 649.895,105.259 648.184,103.661 
 646.424,102.076 644.617,100.504 642.763,98.944 640.86,97.3976 638.909,95.8647 636.91,94.3454 634.862,92.84 632.765,91.3487 630.62,89.8718 628.426,88.4096 
 626.182,86.9622 623.889,85.53 621.545,84.1131 619.152,82.7118 616.709,81.3265 614.214,79.9573 611.669,78.6044 609.072,77.2683 606.424,75.949 603.724,74.6469 
 600.971,73.3622 598.166,72.0952 595.305,70.8466 592.376,69.6182 589.379,68.4105 586.315,67.2232 583.189,66.0563 580.001,64.9096 576.753,63.7834 573.446,62.6774 
 570.082,61.5919 566.661,60.527 563.184,59.4827 559.652,58.4594 556.064,57.4572 552.421,56.4763 548.722,55.5171 544.967,54.58 541.154,53.6652 537.282,52.7733 
 533.35,51.9046 529.357,51.0597 525.3,50.2392 521.177,49.4434 516.987,48.6732 512.725,47.9291 508.389,47.2118 503.977,46.522 499.484,45.8605 494.907,45.2281 
 490.242,44.6256 485.485,44.0539 480.631,43.5139 475.675,43.0066 470.613,42.5329 465.44,42.0939 460.149,41